<a href="https://colab.research.google.com/github/LNickelsburg/title-prediction/blob/main/NLP_Final_Project_Code.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [15]:
!pip install torch torchvision
!pip install -U transformers
!pip install -U simpletransformers
!pip install rouge-score

# New Section

In [16]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [17]:
import pandas as pd
import os

titles = [];
lyrics = [];
dates = [];

def readDetails(fileName):
  data = pd.read_csv('/content/drive/MyDrive/songs/'+fileName)
  global titles
  global lyrics
  global dates

  data_titles = data['Title'].tolist()
  data_lyrics = data['Lyric'].tolist()
  data_dates = data['Date'].tolist()

  if (len(data_titles) > 30) :
    n = 60
    data_titles = data_titles[0:n]
    data_lyrics = data_lyrics[0:n]
    data_dates = data_dates[0:n]

  titles = titles + data_titles
  lyrics = lyrics + data_lyrics
  dates = dates + data_dates



dir = '/content/drive/MyDrive/songs'

for file in os.listdir(dir):
  if file.endswith(".csv"):
    readDetails(file)

titles = list(map(str, titles))
lyrics = list(map(str, lyrics))
dates = list(map(str, dates))
print(len(titles));
print(len(lyrics));
print(len(dates))



1260
1260
1260


In [18]:
songs = pd.DataFrame({
    'title': titles,
    'lyrics': lyrics,
    'date': dates
})
songs.head()

title                                             lyrics  \
0         Shape of You  the club isn't the best place to find a lover ...   
1              Perfect  i found a love for me oh darling just dive rig...   
2   Castle on the Hill  when i was six years old i broke my leg i was ...   
3              Happier  walking down 9th and park i saw you in another...   
4  Supermarket Flowers  i took the supermarket flowers from the window...   

         date  
0  2017-01-06  
1  2017-03-03  
2  2017-01-06  
3  2017-03-03  
4  2017-03-03

In [19]:
songs = songs[['title', 'lyrics', 'date']]
songs.columns = ['target_text', 'input_text', 'date']
print(songs)

songs['prefix'] = "summarize"

eval_df = songs.sample(frac=0.2, random_state=101)
train_df = songs.drop(eval_df.index)

train_df.shape, eval_df.shape
print(eval_df.iloc[100]['date'])

                         target_text  \
0                       Shape of You   
1                            Perfect   
2                 Castle on the Hill   
3                            Happier   
4                Supermarket Flowers   
...                              ...   
1255  ​you don’t get me high anymore   
1256                        ​use me*   
1257                          ​good*   
1258        Thinkin Bout You (Cover)   
1259     COPYCAT (Sofi Tukker Remix)   

                                             input_text        date  
0     the club isn't the best place to find a lover ...  2017-01-06  
1     i found a love for me oh darling just dive rig...  2017-03-03  
2     when i was six years old i broke my leg i was ...  2017-01-06  
3     walking down 9th and park i saw you in another...  2017-03-03  
4     i took the supermarket flowers from the window...  2017-03-03  
...                                                 ...         ...  
1255  billie eilish billie ei

In [20]:
import logging

import pandas as pd
from simpletransformers.t5 import T5Model

logging.basicConfig(level=logging.INFO)
transformers_logger = logging.getLogger("transformers")
transformers_logger.setLevel(logging.WARNING)

model_args = {
    "reprocess_input_data": True,
    "overwrite_output_dir": True,
    "max_seq_length": 200,
    "train_batch_size": 10,
    "num_train_epochs": 1,
}

model = T5Model(model_type="t5", model_name="t5-small", args=model_args, use_cuda=False)
model.train_model(train_df)
results = model.eval_model(eval_df)

print(results)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
/usr/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


  0%|          | 0/1008 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:3946: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 1 of 1:   0%|          | 0/101 [00:00<?, ?it/s]

/usr/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


  0%|          | 0/252 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:3946: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


Running Evaluation:   0%|          | 0/3 [00:00<?, ?it/s]

{'eval_loss': 2.99796724319458}


In [21]:
eval_num = 252

result_titles = [];
original_titles = [];
result_lyrics = [];

for x in range(eval_num):
  actual_title = eval_df.iloc[x]['target_text']
  actual_lyrics = ["summarize: "+eval_df.iloc[x]['input_text']]
  predicted_title = model.predict(actual_lyrics)
  result_titles.append(predicted_title)
  original_titles.append(actual_title)
  result_lyrics.append(actual_lyrics)


print(len(result_titles))

Generating outputs:   0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:4072: FutureWarning: 
`prepare_seq2seq_batch` is deprecated and will be removed in version 5 of HuggingFace Transformers. Use the regular
`__call__` method to prepare your inputs and targets.

Here is a short example:

model_inputs = tokenizer(src_texts, text_target=tgt_texts, ...)

If you either need to use different keyword arguments for the source and target texts, you should do two calls like
this:

model_inputs = tokenizer(src_texts, ...)
labels = tokenizer(text_target=tgt_texts, ...)
model_inputs["labels"] = labels["input_ids"]

See the documentation of your specific tokenizer for more details on the specific arguments to the tokenizer of choice.
For a more complete example, see the implementation of `prepare_seq2seq_batch`.

  warnings.warn(formatted_warning, FutureWarning)
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:563: UserWarning: `num_beams` is set to 1

Decoding outputs:   0%|          | 0/1 [00:00<?, ?it/s]

Generating outputs:   0%|          | 0/1 [00:00<?, ?it/s]

Decoding outputs:   0%|          | 0/1 [00:00<?, ?it/s]

...

Generating outputs:   0%|          | 0/1 [00:00<?, ?it/s]

Decoding outputs:   0%|          | 0/1 [00:00<?, ?it/s]

Generating outputs:   0%|          | 0/1 [00:00<?, ?it/s]

Decoding outputs:   0%|          | 0/1 [00:00<?, ?it/s]

252


In [22]:
print(len(result_titles))
print(len(original_titles))
print(len(result_lyrics))

for x in range(252):
  print(result_titles[x])
  print(original_titles[x])
  print(result_lyrics[x])
  print("\n")


252
252
252
['Older and Wronger']
​tolerate it
["summarize: i sit and watch you reading with your head low i wake and watch you breathing with your eyes closed i sit and watch you i notice everything you do or don't do you're so much older and wiser and i    i wait by the door like i'm just a kid use my best colors for your portrait lay the table with the fancy shit and watch you tolerate it if it's all in my head tell me now tell me i've got it wrong somehow i know my love should be celebrated but you tolerate it   i greet you with a battle hero's welcome i take your indiscretions all in good fun i sit and listеn i polish plates until they gleam and glistеn you're so much older and wiser and i    i wait by the door like i'm just a kid use my best colors for your portrait lay the table with the fancy shit and watch you tolerate it if it's all in my head tell me now tell me i've got it wrong somehow i know my love should be celebrated but you tolerate it   while you were out building ot

In [23]:
import csv
rows = zip(result_titles, original_titles, result_lyrics)

with open('results.csv', 'w', newline='') as file:
    writer = csv.writer(file)

    writer.writerow(['Result Titles', 'Original Titles', 'Lyrics'])

    for row in rows:
        writer.writerow(row)


In [24]:
!pip install python-Levenshtein

In [25]:
import Levenshtein

# EVALUATION METRIC: attempted ROUGE and cosine similarity libraries, did not give meaningful results
# So ended up using Levenshtein Distance:

similarity_scores = []

for x in range(252):
  predicted_text = result_titles[x][0].lower()
  reference_text = original_titles[x][0].lower()
  lev_distance = Levenshtein.distance(predicted_text, reference_text)
  lev_similarity = 1 - (lev_distance / max(len(predicted_title), len(actual_title)))
  similarity_scores.append(lev_similarity)
  print(lev_similarity)



-1.125
-1.625
-0.5
-0.25
0.125
-0.625
0.375
0.375
0.25
0.125
-1.25
0.375
0.625
-0.375
0.5
0.5
0.75
-0.25
0.125
-0.25
-0.375
-2.625
-0.5
-0.125
0.375
-0.375
0.875
-0.125
-0.375
0.25
-0.125
-0.25
-0.375
0.375
-0.125
0.25
-0.75
0.125
0.0
-0.375
-0.625
0.125
0.375
0.125
-0.375
0.25
-1.625
-0.75
-0.75
0.625
-0.375
-0.75
-1.375
-0.5
-0.75
-0.125
-0.625
-0.875
0.75
0.875
0.25
0.75
0.375
0.625
0.5
-0.5
0.25
0.625
0.625
0.375
0.25
0.125
-0.625
-11.25
0.5
0.5
-1.25
-0.5
0.625
0.5
-0.125
0.375
-0.5
-0.25
0.875
0.125
0.5
0.125
0.125
0.25
0.375
0.0
0.625
0.5
-0.375
0.5
-0.5
0.25
0.375
-0.25
-0.75
-0.375
0.25
0.875
-0.375
0.125
0.375
-0.125
0.375
0.375
-0.375
-1.125
0.5
0.0
0.5
0.75
0.75
-0.375
-0.125
0.0
-0.25
0.5
-2.0
0.375
0.375
0.25
-0.375
0.0
0.5
0.625
-0.25
0.0
0.125
-0.625
-0.25
-1.5
0.625
0.75
0.0
-0.125
0.125
-0.25
-0.625
0.25
-0.875
0.125
-1.0
0.375
-2.25
-0.125
-0.375
0.125
0.375
0.875
0.0
0.125
-1.625
0.0
0.625
-1.0
-0.375
0.625
-0.25
0.375
0.0
-1.125
0.25
0.5
-0.875
0.5
0.125
-0.875
0.7